This is not meant as an introductory lecture - this notebook showcases some of the more high-end techniques available to advanced and experienced python users

In [3]:
# pip install rasterstats
# pip install rasterio
# pip install numpy_financial
# pip install loguru
# !git clone https://github.com/Charlesfox1/geo_training

In [4]:
# standard libs
import time
import numpy as np
from loguru import logger
from multiprocessing import Pool, cpu_count

# financial libs
import numpy_financial as npf

# graphical libs
import plotly.express as px

# geospatial libs
from shapely.geometry import Point
import pandas as pd
pd.set_option('display.precision', 1)
import geopandas as gpd
import geo_utils
import rasterio
import rasterstats

### MonteCarlo Simulation
- use python to construct much more advanced scenario simulations

In [5]:
def revenue_growth_pct():
    # Draw from a normal distribution, shifted, mean of 5, s.d. of 1
    return np.random.normal(loc=5, scale=1.0)

def gross_profit_margin_pct():
    # centre around 25%
    return np.random.normal(loc=45, scale=1)

def sg_and_a_growth_pct():
    # Draw from a normal distribution, shifted, mean of 5, s.d. of 1
    return np.random.normal(loc=3, scale=1.0)

def capex_required():
    # Draw from a beta distribution, shifted, mean of 5, s.d. of 1
    x = np.random.beta(a=5, b=5)
    if x > 0.65:
        return True
    else:
        return False
    
def capex_spend():
    # spend of at least 100... could be a lot more...
    return min(np.random.pareto(a=1) * 5 + 100, 5000)

def debt_cost_pct():
    # normal distribution centred on 5%, .s.d 1%, minimum of 2%
    return round(max(np.random.normal(loc=5, scale=1), 2), 1)


def scenario(_input):
    
    V = _input[0]
    years_to_model = _input[1]
    
    # Instantiate local variables
    revenue = V['initial_revenue']
    tax_rate_pct = V['tax_rate_pct']
    debt = V['initial_debt']
    sg_and_a = V['initial_sg_and_a']
    depreciable_assets = V['initial_depreciable_assets']
    depreciation_charge = depreciable_assets * (1 / V['depreciation_lifetime_years'])
    
    res = []
    for year in range(0, years_to_model):
        
        # This year's revenue is last year's multiplied by some growth
        revenue = revenue * ((100 + revenue_growth_pct()) / 100)
        # Gross profit is some fraction of revenue
        gross_margin = gross_profit_margin_pct() / 100
        gross_profit = revenue * gross_margin
        # COGS is the delta
        cogs = revenue - gross_profit
        # Grow SG&A
        sg_and_a = sg_and_a * ((100 + sg_and_a_growth_pct()) / 100)
        # EBITDA
        ebitda = gross_profit - sg_and_a
        # Depreciate assets - straightline (fixed annual charge)
        depreciable_assets -= depreciation_charge
        # EBIT
        ebit = ebitda - depreciation_charge
        # Interest
        if year < V['years_until_refinance']:
            interest_rate_pct = V['initial_interest_pct']
        elif year == V['years_until_refinance']:
            interest_rate_pct = debt_cost_pct()
        interest_charge = debt * ((interest_rate_pct) / 100)
        # Tax
        ebt = ebit - interest_charge
        tax = max(ebt * (tax_rate_pct / 100), 0)
        # PAT
        pat = ebt - tax
        # CAPEX
        if capex_required():
            capex = capex_spend()
        else:
            capex = 0
        # FCFE - Assume no change in Working Capital, Net Borrowing for simplicity
        fcfe = ebitda - interest_charge - tax - capex
        
        # add financials to a list, store
        res.append(
            (year, revenue,cogs,gross_profit,sg_and_a,
             ebitda,depreciation_charge,ebit,interest_rate_pct,
             interest_charge,ebt,tax,pat,capex,fcfe
            )
        )
    
    # generate financials dataframe for this scenario
    df = pd.DataFrame(res, columns = 
                     ['year','revenue','cogs',
                      'gross_profit','sg_and_a','ebitda',
                      'depreciation_charge','ebit','interest_rate',
                      'interest_charge','ebt','tax','pat','capex','fcfe'])
    
    # Define cashflow stream for valuation
    cashflows = [-V['business_purchase_cost']] + list(df['fcfe'])
    
    # Summary dictionary
    summary = {'revenue_cagr': round(((revenue / V['initial_revenue']) ** (1/years_to_model)) - 1,4),
            'avg_gross_margin': round(np.mean(df['gross_profit'] / df['revenue']),4),
            'refinance_interest_rate':round(interest_rate_pct / 100,4),
            'total_capex_as_pct_of_revenue':round(df['capex'].sum() / df['revenue'].sum(),4),
            'sg_and_a_as_pct_of_revenue': round(df['sg_and_a'].sum() / df['revenue'].sum(),4),
            'IRR': round(npf.irr(cashflows),3),
            'NPV': round(npf.npv(V['discount_factor'], cashflows),1)
           }
    
    return summary, df.T

In [6]:
# Set Common Start Variables
V = {
    'initial_revenue':650,
    'tax_rate_pct':20,
    'initial_debt':4000,
    'initial_interest_pct':2,
    'years_until_refinance':5,
    'initial_sg_and_a':45,
    'initial_depreciable_assets':550,
    'depreciation_lifetime_years':10,
    'business_purchase_cost':1000,
    'discount_factor':0.07
}

_input = (V, 10)

scenario(_input)[0]

{'revenue_cagr': 0.0416,
 'avg_gross_margin': 0.4527,
 'refinance_interest_rate': 0.063,
 'total_capex_as_pct_of_revenue': 0.0,
 'sg_and_a_as_pct_of_revenue': 0.0666,
 'IRR': 0.057,
 'NPV': -50.9}

In [7]:
scenario(_input)[1]

0      1      2      3      4      5      6      7  \
year                   0.0    1.0    2.0    3.0    4.0    5.0    6.0    7.0   
revenue              675.6  713.5  752.1  798.6  822.9  872.4  916.8  962.3   
cogs                 364.7  388.4  395.8  437.5  452.2  470.0  490.7  514.3   
gross_profit         310.9  325.1  356.2  361.0  370.7  402.5  426.1  448.0   
sg_and_a              46.4   47.9   49.2   50.6   52.6   52.8   55.1   56.7   
ebitda               264.6  277.2  307.1  310.5  318.0  349.7  371.0  391.3   
depreciation_charge   55.0   55.0   55.0   55.0   55.0   55.0   55.0   55.0   
ebit                 209.6  222.2  252.1  255.5  263.0  294.7  316.0  336.3   
interest_rate          2.0    2.0    2.0    2.0    2.0    5.1    5.1    5.1   
interest_charge       80.0   80.0   80.0   80.0   80.0  204.0  204.0  204.0   
ebt                  129.6  142.2  172.1  175.5  183.0   90.7  112.0  132.3   
tax                   25.9   28.4   34.4   35.1   36.6   18.1   22.4   26.5   
pat                  103.7  113.7  137.7  140.4  146.4   72.6   89.6  105.8   
capex                  0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
fcfe                 158.7  168.7  192.7  195.4  201.4  127.6  144.6  160.8   

                          8       9  
year                    8.0     9.0  
revenue              1006.0  1048.6  
cogs                  571.6   568.6  
gross_profit          434.3   479.9  
sg_and_a               58.9    61.0  
ebitda                375.5   419.0  
depreciation_charge    55.0    55.0  
ebit                  320.5   364.0  
interest_rate           5.1     5.1  
interest_charge       204.0   204.0  
ebt                   116.5   160.0  
tax                    23.3    32.0  
pat                    93.2   128.0  
capex                   0.0     0.0  
fcfe                  148.2   183.0

In [8]:
%%timeit
_ = scenario(_input)[0]

2.85 ms ± 96.9 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


In [9]:
_input = (V, 10)
scenarios = []
financial_dfs = {}
# run 10,000 scenarios
start_time = time.time()
for i in range(10000):
    output = scenario(_input)
    results = output[0]
    results['scenario_id'] = i
    scenarios.append(results)
    financial_dfs[i] = output[1]
end_time = time.time()
print(f'Time elapsed: {round(end_time - start_time, 2)}s')

Time elapsed: 28.99s


In [10]:
# Visualise the results
mdf = pd.DataFrame(scenarios)

In [11]:
mdf

revenue_cagr  avg_gross_margin  refinance_interest_rate  \
0          4.8e-02               0.4                  3.9e-02   
1          5.1e-02               0.4                  5.2e-02   
2          4.5e-02               0.4                  4.5e-02   
3          5.2e-02               0.5                  3.3e-02   
4          5.0e-02               0.5                  6.4e-02   
...            ...               ...                      ...   
9995       5.0e-02               0.4                  5.7e-02   
9996       5.2e-02               0.4                  5.2e-02   
9997       4.8e-02               0.4                  4.4e-02   
9998       4.7e-02               0.4                  6.4e-02   
9999       4.7e-02               0.4                  6.5e-02   

      total_capex_as_pct_of_revenue  sg_and_a_as_pct_of_revenue      IRR  \
0                           0.0e+00                     6.0e-02  1.2e-01   
1                           0.0e+00                     6.2e-02  9.9e-02   
2                           1.6e-02                     6.2e-02  8.8e-02   
3                           5.2e-02                     6.1e-02  7.7e-02   
4                           1.3e-02                     6.1e-02  7.0e-02   
...                             ...                         ...      ...   
9995                        0.0e+00                     6.3e-02  9.0e-02   
9996                        1.2e-02                     6.0e-02  8.2e-02   
9997                        3.6e-02                     6.1e-02  6.8e-02   
9998                        3.8e-02                     6.4e-02  1.0e-02   
9999                        1.2e-02                     6.3e-02  5.0e-02   

        NPV  scenario_id  
0     240.7            0  
1     134.8            1  
2      80.6            2  
3      35.7            3  
4       0.3            4  
...     ...          ...  
9995   87.6         9995  
9996   57.5         9996  
9997   -8.5         9997  
9998 -260.7         9998  
9999  -74.9         9999  

[10000 rows x 8 columns]

### Options
- Visualise scenarios by condition (e.g. count of scenarios by IRR)
- Investigate this dataset with regression / PCA

In [13]:
# Example / Starter: Visualise scenarios by IRR, colour by different variables
x = 'IRR'
y = 'avg_gross_margin'
fig = px.scatter(mdf, 
                 x=x, 
                 y=y,
                 hover_data=['scenario_id'])
fig.update_xaxes(range=[-0.1,0.2], title = x)
fig.update_yaxes(title = y)
fig.update_layout(height = 800, width = 1000)
fig.show()

#### Conclusion - not a huge relationship between IRR and gross margin - something else might be more important

In [14]:
# Example / Starter: Visualise scenarios by IRR, colour by different variables
x = 'IRR'
y = 'refinance_interest_rate'
fig = px.scatter(mdf, 
                 x=x, 
                 y=y,
                 hover_data=['scenario_id'])
fig.update_xaxes(range=[-0.1,0.2], title = x)
fig.update_yaxes(title = y)
fig.update_layout(height = 800, width = 1000)
fig.show()

#### Conclusion - strong negative relationship between IRR and Refinance interest rate
- more important to watch refinancing for this company than margin progression

In [27]:
# Example / Starter: Visualise scenarios by IRR, colour by different variables
x = 'IRR'
y = 'total_capex_as_pct_of_revenue'
fig = px.scatter(mdf, 
                 x=x, 
                 y=y,
                 hover_data=['scenario_id'])
fig.update_xaxes(range=[-0.1,0.2], title = x)
fig.update_yaxes(range=[0,0.1], title = y)
fig.show()

In [28]:
# Example / Starter: Visualise scenarios by IRR, colour by different variables
x = 'IRR'
y = 'total_capex_as_pct_of_revenue'
fig = px.scatter(mdf, 
                 x=x, 
                 y=y,
                 color='refinance_interest_rate',
                 hover_data=['scenario_id'])
fig.update_xaxes(range=[-0.1,0.2], title = x)
fig.update_yaxes(range=[0,0.1], title = y)
fig.show()

### Multithreading: Use the Whole Computer
- Distribute independent tasks across available threads - e.g, montecarlo simulations!

In [16]:
# Find out what compute we have available
cpus = cpu_count()
logger.info(f"Detected {cpus} cores on the machine")

def f(x):
    # Simple work function
    return x*x

# Bundle of inputs
number_of_scenarios = range(1000)

# Ensure entry at master process level
if __name__ == '__main__':
    
    # Create a CPU pool
    with Pool(cpus) as p:
        
        results = p.map(f, number_of_scenarios)

2023-10-01 11:22:58.233 | INFO     | __main__:<module>:3 - Detected 4 cores on the machine


In [ ]:
print(len(results))

In [ ]:
results[:5]

- Now let's run our Montecarlo simulation, but multi-threaded

In [19]:
# Find out what compute we have available
cpus = cpu_count()
logger.info(f"Detected {cpus} cores on the machine")

# Bundle of inputs
number_of_scenarios = 10000

# Ensure entry at master process level
if __name__ == '__main__':
    
    start_time = time.time()
    
    # Create a CPU pool
    with Pool(cpus) as p:
        
        # map the work to the pool, gather the results
        scenarios_pooled = p.map(scenario, [(V, 10)]*number_of_scenarios)
    
    end_time = time.time()
    print(f'Time elapsed: {round(end_time - start_time, 2)}s when distributed across {cpus} CPUs')

2023-10-01 11:23:47.955 | INFO     | __main__:<module>:3 - Detected 4 cores on the machine


Time elapsed: 10.99s when distributed across 4 CPUs


### Optimisation
- Use 3rd party optimizers to solve problems with constraints

### Geospatial Data
- Use geospatial data to sense-check company expansion plans, optimise real estate positioning, etc. 
- Schroders has expanded and has decided to launch a range of cheap Scandinanvian furniture ("SchroKEA"). they have identified 10 potential locations in London for their first store. Which location gives them the greatest addressable market in 20 minutes?

In [ ]:
# Import locations
locations = gpd.read_file('geo_training/locations.geojson')
locations = locations.set_index('id')

# Use TravelTime API service to generate 20-minute isochrone

creds = {'X-Application-Id':os.getenv('X_APPLICATION_ID'),
         'X-Api-Key':os.getenv('X_API_KEY')}
        
travel_time_mins = 20
isos = []
for _id_, location in locations.iterrows():
    
    iso = geo_utils.tt_isochrone(location.geometry, 
                                 travel_time_mins = 20,
                                 creds = creds, # I can't share these!
                                 mode = 'public_transport',
                                 _id_ = str(_id_)
                                )
    
    isos.append(iso)
    


In [210]:
iso_gdf = gpd.GeoDataFrame(pd.concat(isos), crs = 4326, geometry = 'geometry')
iso_gdf.index = iso_gdf.index.astype(int)
iso_gdf = iso_gdf.join(locations[['location']]).reset_index()
iso_gdf.to_file('geo_training/isochrones.geojson')

In [245]:
# let's visualise our isochrones for each location, in a different colour each time
colour_map = {1:"rgb(0,42,94)",
             2:"rgb(0,121,109)",
             3:"rgb(234,82,4)",
             4:"rgb(183,25,98)",
             5:"rgb(79,51,152)",
             6:"rgb(0,116,183)",
             7:"rgb(99,197,50)",
             8:"rgb(248,169,8)",
             9:"rgb(223,83,106)",
             10:"rgb(125,55,135)"}

import folium
m = folium.Map(location=[51.5074, -0.1278], zoom_start=12)  

# Define the style function  
def style_function(feature):  
    
    # Get the value for coloring from the feature properties  
    value = feature['properties']['search_id']
      
    # Get the color based on the value using the color map  
    colour = colour_map.get(value) 
      
    # Return the style properties  
    return {  
        'fillColor': colour,  
        'color': 'black',  
        'weight': 1,  
        'fillOpacity': 0.6,
    }  

folium.GeoJson(iso_gdf, 
               style_function=style_function,
               tooltip=folium.GeoJsonTooltip(fields=['location'])
            ).add_to(m)

display(m)  

In [257]:
# Now, let's import a population dataset so we can see which isochrone affords us the biggest market
with rasterio.open('clipped_GBR_worldpop.tif') as r:
    arr = r.read(1)
    arr[arr<0] = 0
    aff = r.meta['transform']

In [258]:
# what does the population data look like "under the hood"?
arr

array([[  0.       ,   0.       ,   7.271873 , ...,   8.592625 ,
          4.4721594,  15.676467 ],
       [  0.       ,   2.4741092,   2.653108 , ...,   3.007857 ,
          2.1524282,   3.0818932],
       [  7.0299067,   6.999458 ,   7.178957 , ...,   1.4412255,
          1.5851892,   1.401784 ],
       ...,
       [ 75.75786  ,  76.0401   , 172.76715  , ...,   5.263302 ,
          8.858702 ,   4.4420295],
       [ 74.39615  ,  72.13014  ,  76.62575  , ...,  15.044149 ,
          2.0365822,   1.207004 ],
       [ 76.76962  ,  75.5393   ,  59.569084 , ...,  14.02362  ,
          1.991469 ,   1.2088212]], dtype=float32)

In [260]:
arr.shape

(154, 346)

In [261]:
aff

Affine(0.0008333333300256081, 0.0, -0.24124998371158846,
       0.0, -0.00083333333002425, 51.57291666154971)

In [263]:
# sample raster for each polygon in iso_gdf
zs = rasterstats.zonal_stats(iso_gdf, arr, affine=aff, stats=['sum'])
iso_gdf['20_min_pop'] = [i['sum'] for i in zs]
iso_gdf = iso_gdf.sort_values(by = '20_min_pop', ascending = False)
iso_gdf

search_id                                           geometry  \
7          8  MULTIPOLYGON (((-0.11584 51.51488, -0.11728 51...   
8          9  MULTIPOLYGON (((-0.23408 51.54591, -0.22976 51...   
4          5  MULTIPOLYGON (((-0.14606 51.51308, -0.13886 51...   
6          7  MULTIPOLYGON (((-0.10298 51.51903, -0.10154 51...   
0          1  MULTIPOLYGON (((-0.19282 51.47669, -0.19210 51...   
1          2  MULTIPOLYGON (((-0.17711 51.52944, -0.17711 51...   
2          3  MULTIPOLYGON (((-0.15765 51.50928, -0.15477 51...   
3          4  MULTIPOLYGON (((-0.16195 51.48507, -0.16051 51...   
9         10  MULTIPOLYGON (((-0.08063 51.51240, -0.08063 51...   
5          6  MULTIPOLYGON (((-0.03814 51.51390, -0.03958 51...   

          location  20_min_pop  
7  Elephant&Castle    218371.6  
8          Kilburn    195790.6  
4             Bank    119317.0  
6       Shoreditch     99720.9  
0          Chelsea     96939.1  
1       Marylebone     94409.0  
2             Soho     87073.0  
3      Westminster     58009.1  
9          Wapping     55027.2  
5       IsleofDogs     51226.4

- SchrodKEA should set up shop in E&C and Kilburn first, rather than somewhere more central like Westminster - due to a combination of the immediate resident population density + public transport availability

### Alternative Data - Web Scraping
- Gather non-standard data from the internet to augment traditional decision making
- e.g. gather all the property information on this webpage: https://www.rexfordindustrial.com/properties

In [96]:
import requests
from bs4 import BeautifulSoup

In [31]:
url = 'https://www.rexfordindustrial.com/properties'
r = requests.get(url)

In [35]:
soup = BeautifulSoup(r.content, 'html')

In [40]:
all_prop_divs = soup.find('div', attrs = {'class':'properties-listing'}).find_all('article')

In [57]:
prop_collection = []
for a in all_prop_divs:
    p = {'prop_name':a.find('h1').text,
         'location':a.find('h2').text,
         'available_space':a.find_all('h3')[0].text,
         'total_space':a.find_all('h3')[1].text
         }
    prop_collection.append(p)  

We can use this alternative data to track concepts of interest to us...e.g.:
- "What is the fraction of total space, across all warehouse properties, that is currently vacanct?
- "Which property has the highest vacancy rate?
- "Any patterns / identifying factors for the most vacant properties"?

In [101]:
pdf = pd.DataFrame(prop_collection)

pdf['available_space'].str.split(' ').str[0].str.replace(', ','')

pdf['available_space'] = pd.to_numeric(pdf['available_space'].str.split(' ').str[0].str.replace(',',''), 
                                       errors = 'coerce').fillna(0)

pdf['total_space'] = pd.to_numeric(pdf['total_space'].str.split(' ').str[0].str.replace(',',''), 
                                       errors = 'coerce').fillna(0)

overall_vacancy_rate = pdf['available_space'].sum() / pdf['total_space'].sum()

str(round(overall_vacancy_rate * 100, 2))+' percent'

'3.83 percent'

In [102]:
pdf['vacancy_rate'] = (pdf['available_space'] / pdf['total_space']) * 100
pdf.sort_values(by = 'vacancy_rate', ascending = False).head(20)

prop_name               location  available_space  \
253               20851 Currier Road   City of Industry, CA           59436.0   
125              2800 Casitas Avenue        Los Angeles, CA          116158.0   
310            15401 Figueroa Street        Los Angeles, CA           38584.0   
153             3071 Coronado Street            Anaheim, CA          105173.0   
351              8240 Haskell Avenue           Van Nuys, CA           11987.0   
353             422 Rosecrans Avenue            Gardena, CA            9350.0   
331             400 Rosecrans Avenue            Gardena, CA           28006.0   
335              8210 Haskell Avenue           Van Nuys, CA           26229.0   
334                  444 Quay Avenue        Los Angeles, CA           26700.0   
263             21515 Western Avenue           Torrance, CA           56199.0   
28                 500 Dupont Avenue            Ontario, CA          274885.0   
120                404-430 Berry Way               Brea, CA          101380.0   
169                 9455 Cabot Drive          San Diego, CA           83563.0   
289         9755 Distribution Avenue          San Diego, CA           23726.0   
123     14434-14527 San Pedro Street        Los Angeles, CA           58094.0   
78                 Penrose - Tujunga         Sun Valley, CA           71547.0   
119       21605-21615 Plummer Street         Chatsworth, CA           40582.0   
146  9641-9657 Santa Fe Springs Road   Santa Fe Springs, CA           34205.0   
306              960-970 Knox Street           Torrance, CA           10700.0   
18          1600 Orangethorpe Avenue          Fullerton, CA           93654.0   

     total_space  vacancy_rate  
253      59000.0         100.7  
125     116158.0         100.0  
310      38584.0         100.0  
153     105173.0         100.0  
351      11987.0         100.0  
353       9350.0         100.0  
331      28006.0         100.0  
335      26229.0         100.0  
334      26700.0         100.0  
263      56199.0         100.0  
28      274898.0         100.0  
120     120250.0          84.3  
169      99403.0          84.1  
289      47666.0          49.8  
123     118923.0          48.9  
78      151011.0          47.4  
119     120594.0          33.7  
146     106995.0          32.0  
306      39400.0          27.2  
18      345756.0          27.1

pdf

In [103]:
pdf[pdf['vacancy_rate'] > 80].total_space.mean().round(0)

74764.0

In [104]:
pdf[pdf['vacancy_rate'] < 80].total_space.mean().round(0)

131146.0

In [105]:
pdf.total_space.mean().round(0)

126659.0

...The vacant properties are significantly smaller than average for Rexford... are smaller properties harder to lease, or do they have a higher turnover rate?

### Bonus: Machine Learning
- Harness cutting-edge techniques to make predictions for variables of interest
- Better to use Kaggle than look at something I put together! https://www.kaggle.com/code/janiobachmann/credit-fraud-dealing-with-imbalanced-datasets 